updated May 1st, 2017 for OGD integration study
fetch 
- 1) all soda sites metadata  
- 2) crime data from interesting cities listed in http://www.sciencedirect.com/science/article/pii/S0740624X16301071

- San Francisco
- Austin
- Baltimore
- New York
- Seattle
- Chicago
- Honolulu
- Los Angeles
- Raleigh
- Kansas City
- Belleville,Illinois

In [60]:
import numpy as np;
from sodapy import Socrata
import json
from urllib2 import Request, urlopen
import pprint
import urllib
import pandas as pd
import codecs

https://github.com/xmunoz/sodapy#getdataset_identifier-content_typejson-kwargs

https://dev.socrata.com/docs/queries/

https://data.seattle.gov/browse?federation_filter=2&utf8=%E2%9C%93

http://docs.socratadiscovery.apiary.io/#reference/0/count-by-and-list-categories/custom-metadata-search-api

http://docs.socratadiscovery.apiary.io/#reference/0/count-by-and-list-categories/custom-metadata-search-api

### Get the count of datasets and count of Crime datasets in the cities of interests

In [11]:
request2 = Request('http://api.us.socrata.com/api/catalog/v1/domains')
response_body = json.loads(urlopen(request2).read())
result = response_body['results']
pprint.pprint(result) 

[{u'count': 4, u'domain': u'2014bonds.cityofws.org'},
 {u'count': 66, u'domain': u'amopen.amo.on.ca'},
 {u'count': 84, u'domain': u'bchi.bigcitieshealth.org'},
 {u'count': 3, u'domain': u'bea.data.commerce.gov'},
 {u'count': 2, u'domain': u'bis.data.commerce.gov'},
 {u'count': 494, u'domain': u'brigades.opendatanetwork.com'},
 {u'count': 751, u'domain': u'bronx.lehman.cuny.edu'},
 {u'count': 111, u'domain': u'bythenumbers.sco.ca.gov'},
 {u'count': 212, u'domain': u'census.data.commerce.gov'},
 {u'count': 477, u'domain': u'chhs.data.ca.gov'},
 {u'count': 389, u'domain': u'chronicdata.cdc.gov'},
 {u'count': 7, u'domain': u'cip.cityofnovi.org'},
 {u'count': 975, u'domain': u'controllerdata.lacity.org'},
 {u'count': 334, u'domain': u'dashboard.alexandriava.gov'},
 {u'count': 282, u'domain': u'dashboard.edmonton.ca'},
 {u'count': 943, u'domain': u'dashboard.hawaii.gov'},
 {u'count': 112, u'domain': u'dashboard.plano.gov'},
 {u'count': 46, u'domain': u'dashboard.slco.org'},
 {u'count': 264, 

In [41]:
all_cities_df = pd.DataFrame(result)
url_list = ['data.baltimorecity.gov','data.cityofchicago.org','data.austintexas.gov',
                  'data.raleighnc.gov','data.kcmo.org','data.lacity.org',
                  'data.illinois.gov','data.sfgov.org','data.seattle.gov',
                  'data.cityofnewyork.us','data.honolulu.gov']
cityname_list =['baltimorecity','cityofchicago','austintexas','raleighnc','kcmo','lacity',
               'belleville','sf','seattle','cityofnewyork','honolulu']
cities_df = all_cities_df[all_cities_df['domain'].isin (url_list)]

# cities_df['city'] = cityname_list
cities_df['count']=cities_df['count'].astype(int)
cities_df =cities_df.sort_values(['count'],ascending=False)
cities_df

/Users/yanan/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


count                  domain
41   10463   data.cityofnewyork.us
80    5003           data.kcmo.org
134   2925        data.seattle.gov
24    2133  data.baltimorecity.gov
22    1457    data.austintexas.gov
36    1146  data.cityofchicago.org
135    912          data.sfgov.org
125    738      data.raleighnc.gov
76     651       data.illinois.gov
83     482         data.lacity.org
75     167       data.honolulu.gov

In [42]:
# get crime count
# fetch seattle public safety data
# tags = crime, datasets only
url ="http://api.us.socrata.com/api/catalog/v1?domains=data.seattle.gov&tags=crime&categories=public%20safety&search_context=data.seattle.gov&only=datasets"
response = urllib.urlopen(url)
data = json.loads(response.read())
# pprint.pprint(data) 
result_size =data['resultSetSize'] 
# print result_size


6


In [46]:
# full text fetch "crime"
url = "http://api.us.socrata.com/api/catalog/v1?domains=data.seattle.gov&q=crime&search_context=data.seattle.gov&only=datasets"
response = urllib.urlopen(url)
data = json.loads(response.read())
# pprint.pprint(data) 
result_size =data['resultSetSize'] 
# print result_size

8


In [44]:
# get crime datasets
# use "categories=public%20safety"
# some cities crime datasets do not have any tags, 
# la uses "A+Safe+City", kansas use "crime"
# some even do not have categories
# i.e., https://data.honolulu.gov/dataset/HPD-Crime-Incidents/f5dd-pqys
url_set = set(url_list)
for city in url_set:
    print("city",city)
    crime_base_url="http://api.us.socrata.com/api/catalog/v1?domains="+city+"&categories=public%20safety&search_context="+city+"&only=datasets"
    response = urllib.urlopen(crime_base_url)
    data = json.loads(response.read())
    # pprint.pprint(data) 
    result_size =data['resultSetSize'] 
    print result_size

('city', 'data.austintexas.gov')
62
('city', 'data.seattle.gov')
24
('city', 'data.sfgov.org')
6
('city', 'data.lacity.org')
0
('city', 'data.kcmo.org')
0
('city', 'data.baltimorecity.gov')
10
('city', 'data.illinois.gov')
13
('city', 'data.cityofnewyork.us')
152
('city', 'data.honolulu.gov')
1
('city', 'data.raleighnc.gov')
2
('city', 'data.cityofchicago.org')
7


In [49]:
# get crime datasets
# use full text match search "crime"
# Assets may be searched by any of the text found in the name, 
#description, category, column names, column fieldnames and column descriptions
url_set = set(url_list)
for city in url_set:
    print("city",city)
    crime_base_url="http://api.us.socrata.com/api/catalog/v1?domains="+city+"&q=crime&search_context="+city+"&only=datasets"
    response = urllib.urlopen(crime_base_url)
    data = json.loads(response.read())
    # pprint.pprint(data) 
    result_size =data['resultSetSize'] 
    print result_size
    cities_df.loc[cities_df['domain']==city,'crime_ds_count']=result_size

('city', 'data.austintexas.gov')
19
('city', 'data.seattle.gov')
8
('city', 'data.sfgov.org')
2
('city', 'data.lacity.org')
4
('city', 'data.kcmo.org')
17
('city', 'data.baltimorecity.gov')
7
('city', 'data.illinois.gov')
7
('city', 'data.cityofnewyork.us')
14
('city', 'data.honolulu.gov')
2
('city', 'data.raleighnc.gov')
2
('city', 'data.cityofchicago.org')
5


In [51]:
# get crime maps
# use full text match search "crime"
# Assets may be searched by any of the text found in the name, 
#description, category, column names, column fieldnames and column descriptions
url_set = set(url_list)
for city in url_set:
    print("city",city)
    crime_base_url="http://api.us.socrata.com/api/catalog/v1?domains="+city+"&q=crime&search_context="+city+"&only=maps"
    response = urllib.urlopen(crime_base_url)
    data = json.loads(response.read())
    # pprint.pprint(data) 
    result_size =data['resultSetSize'] 
    cities_df.loc[cities_df['domain']==city,'crime_map_count']=result_size
    print result_size

('city', 'data.austintexas.gov')
2
('city', 'data.seattle.gov')
205
('city', 'data.sfgov.org')
4
('city', 'data.lacity.org')
0
('city', 'data.kcmo.org')
35
('city', 'data.baltimorecity.gov')
232
('city', 'data.illinois.gov')
2
('city', 'data.cityofnewyork.us')
20
('city', 'data.honolulu.gov')
0
('city', 'data.raleighnc.gov')
19
('city', 'data.cityofchicago.org')
3


In [58]:
# maybe add columns such as population, state, portal creation date
cities_df.reset_index(drop=True)

count                  domain  crime_ds_count  crime_map_count
0   10463   data.cityofnewyork.us            14.0             20.0
1    5003           data.kcmo.org            17.0             35.0
2    2925        data.seattle.gov             8.0            205.0
3    2133  data.baltimorecity.gov             7.0            232.0
4    1457    data.austintexas.gov            19.0              2.0
5    1146  data.cityofchicago.org             5.0              3.0
6     912          data.sfgov.org             2.0              4.0
7     738      data.raleighnc.gov             2.0             19.0
8     651       data.illinois.gov             7.0              2.0
9     482         data.lacity.org             4.0              0.0
10    167       data.honolulu.gov             2.0              0.0

## get a list of crime datasets metadata from 
http://us-city.census.okfn.org/dataset/crime-stats and manual selection
scripts from https://github.com/annieyan/urban-data-study/blob/master/metadata/get_metadata.py

In [65]:
crime_ds_urls = list()
with open('crime_ds_urls.txt','r') as f:
    for i,line in enumerate(f):
        crime_ds_urls.append(line.strip())

In [77]:
# http://data.austintexas.gov/api/views/spbg-9v94.json
date = '05022017'
path = 'crime_md/'
schema_path='schema/'
meta_path ='metadata/'
for item in set(crime_ds_urls):
    item_parts = item.split('/')
    dataset_id = item_parts[-1]
    portal_url = 'https://'+item_parts[2]
    md_url=portal_url+'/api/views/'+dataset_id+'.json'
    response = urllib.urlopen(md_url)
    md_data = json.loads(response.read())
    # write original metadata to file
    md_filename = item_parts[2]+'_'+dataset_id+'_'+date+'.txt'
    with open(path+md_filename, 'w') as outfile:
        json.dump(md_data, outfile)
    schema_f = codecs.open(schema_path + item_parts[2]+'_'+dataset_id+'_'+date+'_schema.csv', 'a', 'utf-8')
    meta_f = codecs.open(meta_path + item_parts[2]+'_'+dataset_id+'_'+date+'_metadata.csv', 'a', 'utf-8')

    #Get metadata of each dataset
    #ID and NAME
    id = md_data['id']
    meta = id + '\t' + md_data['name']
      
    #DESCRIPTION
    if md_data.has_key('description'):
        meta_f.write(meta + "\t" + md_data['description'].replace('\n', ' ') + "\n")
    
    #Get schema of each dataset
    schemaurl = md_url
    aJS = md_data
    if aJS.has_key('columns'):
        schema_js = aJS['columns']
#         schema = md_data['id']
        fieldName = ''
        dataTypeName=  ''
        description = ''
        position =''
        if schema_js != None:
            for field in schema_js:
                fieldName = fieldName + ',' + field['fieldName']
                dataTypeName = dataTypeName + ',' + field['dataTypeName']
                if field.has_key('description'):
                    description = description + ',' + field['description']
                else:
                    description =description+','+''
                position = position + ',' + str(field['position'])
                
                
            schema_f.write(fieldName + '\n')
            schema_f.write(dataTypeName + '\n')
            schema_f.write(description + '\n')
            schema_f.write(position + '\n')
            
        else:
            print md_data['id']
      
    print 'Done'
print 'Done'
meta_f.close()
schema_f.close()
    
    

Done
Done
Done
Done
Done
Done
Done
Done
Done
Done
Done
Done
Done
Done
Done
Done
Done
Done
Done


# deprecated #

In [ ]:

request = Request('http://api.us.socrata.com/api/catalog/v1?domains=data.seattle.gov&offset=0&limit=10000')

response_body = json.loads(urlopen(request).read())
result = response_body['results']
pprint.pprint(result) 

[{u'classification': {u'categories': [],
                      u'domain_category': u'Transportation',
                      u'domain_metadata': [{u'key': u'Refresh-Frequency_Frequency',
                                            u'value': u''},
                                           {u'key': u'Data-Owner_Owner',
                                            u'value': u'Department of Transportation'}],
                      u'domain_tags': [u'road',
                                       u'seattle',
                                       u'street',
                                       u'temperature',
                                       u'transportation',
                                       u'weather'],
                      u'tags': []},
  u'link': u'https://data.seattle.gov/Transportation/Road-Weather-Information-Stations/egc4-d24i',
  u'metadata': {u'domain': u'data.seattle.gov'},
  u'permalink': u'https://data.seattle.gov/d/egc4-d24i',
  u'resource': {u'attribution': u'Dep

In [16]:
with open('seattle-catalog_121116.json', 'w') as outfile:
    json.dump(result, outfile)

In [8]:
request6 = Request('http://api.us.socrata.com/api/catalog/v1?domains=data.cityofchicago.org')

response_body6 = json.loads(urlopen(request6).read())
result6 = response_body6['results']
with open('chicago-catalog_112316.json', 'w') as outfile:
    json.dump(result6, outfile)

In [5]:
request2 = Request('http://api.us.socrata.com/api/catalog/v1/domains')

response_body2 = urlopen(request2).read()
print response_body2

{
  "results" :
    [
      { "domain" : "2014bonds.cityofws.org", "count" : 4 },
      { "domain" : "amopen.amo.on.ca", "count" : 66 },
      { "domain" : "bchi.bigcitieshealth.org", "count" : 84 },
      { "domain" : "bea.data.commerce.gov", "count" : 3 },
      { "domain" : "bis.data.commerce.gov", "count" : 2 },
      { "domain" : "brigades.opendatanetwork.com", "count" : 494 },
      { "domain" : "bronx.lehman.cuny.edu", "count" : 751 },
      { "domain" : "bythenumbers.sco.ca.gov", "count" : 111 },
      { "domain" : "census.data.commerce.gov", "count" : 212 },
      { "domain" : "chhs.data.ca.gov", "count" : 475 },
      { "domain" : "chronicdata.cdc.gov", "count" : 389 },
      { "domain" : "cip.cityofnovi.org", "count" : 7 },
      { "domain" : "controllerdata.lacity.org", "count" : 975 },
      { "domain" : "dashboard.alexandriava.gov", "count" : 334 },
      { "domain" : "dashboard.edmonton.ca", "count" : 282 },
      { "domain" : "dashboard.hawaii.gov", "count" : 943 },
   

In [10]:
client2 = Socrata("data.seattle.gov", None)
client2.get_metadata("9nka-b3jn")
# https://data.seattle.gov/resource/9nka-b3jn.json

{u'attribution': u'SDOT',
 u'averageRating': 0,
 u'category': u'Transportation',
 u'columns': [{u'dataTypeName': u'calendar_date',
   u'fieldName': u'date',
   u'format': {},
   u'id': 190014323,
   u'name': u'Date',
   u'position': 1,
   u'renderTypeName': u'calendar_date',
   u'tableColumnId': 24767993,
   u'width': 148},
  {u'dataTypeName': u'number',
   u'fieldName': u'bgt_north_of_ne_70th_total',
   u'format': {},
   u'id': 190014324,
   u'name': u'BGT North of NE 70th Total',
   u'position': 2,
   u'renderTypeName': u'number',
   u'tableColumnId': 24767994,
   u'width': 238},
  {u'dataTypeName': u'number',
   u'fieldName': u'ped_south',
   u'format': {},
   u'id': 190014325,
   u'name': u'Ped South',
   u'position': 3,
   u'renderTypeName': u'number',
   u'tableColumnId': 24767995,
   u'width': 208},
  {u'dataTypeName': u'number',
   u'fieldName': u'ped_north',
   u'format': {},
   u'id': 190014326,
   u'name': u'Ped North',
   u'position': 4,
   u'renderTypeName': u'number',
   

In [6]:
request3 = Request('http://api.us.socrata.com/api/catalog/v1')

#response_body3 = json.loads(urlopen(request3).read())
response_body3 = urlopen(request3).read()
#result3 = response_body3['results']
print response_body3

{
  "results" :
    [
      {
        "resource" :
          {
            "provenance" : "community",
            "description" : "Data of approved building/construction permits",
            "page_views" :
              {
                "page_views_total" : 7728984,
                "page_views_total_log" : 22.881847535658856,
                "page_views_last_week" : 312051,
                "page_views_last_month_log" : 19.658340508242922,
                "page_views_last_month" : 827465,
                "page_views_last_week_log" : 18.251426932662614
              },
            "columns_field_name" :
              [
                "comments",
                "permittypedescr",
                "permitnumber",
                "worktype",
                "city",
                "declared_valuation",
                "property_id",
                "state",
                "occupancytype",
                "issued_date",
                "total_fees",
                "address",
          

In [12]:
with open('all-sodacatalog_112316.json', 'w') as outfile:
    json.dump(result3, outfile)

In [13]:
request4 = Request('http://api.us.socrata.com/api/catalog/v1/domain_categories')

response_body4 = urlopen(request4).read()
print response_body4

{
  "results" :
    [
      { "domain_category" : "", "count" : 24312 },
      { "domain_category" : "Earth Science", "count" : 22941 },
      { "domain_category" : "Public Safety", "count" : 4360 },
      { "domain_category" : "Government", "count" : 4164 },
      { "domain_category" : "Social Services", "count" : 4118 },
      { "domain_category" : "Transportation", "count" : 2582 },
      { "domain_category" : "Health", "count" : 2383 },
      { "domain_category" : "City Government", "count" : 1889 },
      { "domain_category" : "Education", "count" : 1578 },
      { "domain_category" : "Drug Utilization", "count" : 1455 },
      { "domain_category" : "Environment", "count" : 1163 },
      { "domain_category" : "Loans and Credits", "count" : 1136 },
      { "domain_category" : "Energy & Environment", "count" : 1062 },
      { "domain_category" : "Community", "count" : 963 },
      { "domain_category" : "Business", "count" : 941 },
      { "domain_category" : "Housing & Development",

In [14]:
request5 = Request('http://api.us.socrata.com/api/catalog/v1/domains/data.seattle.gov/facets')

response_body5 = urlopen(request5).read()
print response_body5

[
  {
    "facet" : "datatypes",
    "count" : 2738,
    "values" :
      [
        { "value" : "filter", "count" : 1597 },
        { "value" : "map", "count" : 761 },
        { "value" : "dataset", "count" : 184 },
        { "value" : "chart", "count" : 68 },
        { "value" : "href", "count" : 58 },
        { "value" : "form", "count" : 28 },
        { "value" : "file", "count" : 24 },
        { "value" : "datalens", "count" : 10 },
        { "value" : "calendar", "count" : 7 },
        { "value" : "story", "count" : 1 }
      ]
  },
  {
    "facet" : "categories",
    "count" : 2631,
    "values" :
      [
        { "value" : "Public Safety", "count" : 1285 },
        { "value" : "Community", "count" : 382 },
        { "value" : "Transportation", "count" : 293 },
        { "value" : "Permitting", "count" : 259 },
        { "value" : "Land Base", "count" : 146 },
        { "value" : "Parks and Recreation", "count" : 119 },
        { "value" : "Finance", "count" : 85 },
        { "v

In [15]:
request6 = Request('http://api.us.socrata.com/api/catalog/v1?only=datasets')

response_body6 = urlopen(request6).read()
print response_body6

{
  "results" :
    [
      {
        "resource" :
          {
            "provenance" : "community",
            "description" : "Data of approved building/construction permits",
            "page_views" :
              {
                "page_views_total" : 7728984,
                "page_views_total_log" : 22.881847535658856,
                "page_views_last_week" : 312051,
                "page_views_last_month_log" : 19.658340508242922,
                "page_views_last_month" : 827465,
                "page_views_last_week_log" : 18.251426932662614
              },
            "columns_field_name" :
              [
                "comments",
                "permittypedescr",
                "permitnumber",
                "worktype",
                "city",
                "declared_valuation",
                "property_id",
                "state",
                "occupancytype",
                "issued_date",
                "total_fees",
                "address",
          

## metrics ##

In [18]:
# retreive site wide data
# start_time = 1357027200000
# end_time = 1480579200000
# time_step = 604800000
request = Request('https://data.seattle.gov/api/site_metrics.json?start=1357027200000&end=1480579200000&method=series&slice=WEEKLY')

response_body = json.loads(urlopen(request).read())

pprint.pprint(response_body) 

[{u'__end__': 1357430399999,
  u'__start__': 1356825600000,
  u'metrics': {u'app-token-created': 1,
               u'bytes-in': 69159390,
               u'bytes-out': 41983019721,
               u'charts-created': 7,
               u'charts-deleted': 7,
               u'datasets-created': 55,
               u'datasets-deleted': 54,
               u'disk-usage': 3200769076,
               u'filters-created': 817,
               u'filters-deleted': 816,
               u'maps-created': 612,
               u'maps-deleted': 611,
               u'page-views': 16112,
               u'rows-accessed-api': 33921,
               u'rows-accessed-download': 833,
               u'rows-accessed-print': 61,
               u'rows-accessed-rss': 3560,
               u'rows-accessed-website': 7867,
               u'rows-accessed-widget': 1269,
               u'rows-created': 10413882,
               u'rows-deleted': 9697312,
               u'rows-loaded-api': 2158633,
               u'rows-loaded-downloa

In [19]:
with open('seattle-site_stat_121116.json', 'w') as outfile:
    json.dump(response_body, outfile)